In [22]:
# Importar librería para la conexión con MySQL
# -----------------------------------------------------------------------
#pip install requests-> en caso de no tenerla
#pip install pandas-> en caso de no tenerla
#pip install numpy-> en caso de no tenerla
import requests
import pandas as pd

# conexion a spotify
# -----------------------------------------------------------------------
%pip install spotipy
import spotipy
from spotipy.oauth2 import SpotifyClientCredentials
import json

Note: you may need to restart the kernel to use updated packages.


In [23]:
#Nuestras credenciales
client_id = "d92d4d48fda645fd8b4db00c59b653bf"
client_secret = "d891b054de0a438b86d6438f456a49fd"

In [24]:
# Autentificación
auth_manager = SpotifyClientCredentials(client_id=client_id, client_secret=client_secret)
sp = spotipy.Spotify(auth_manager=auth_manager)

In [41]:
def get_track_info(tracks, genere):
    return [
        {
            "genero": f"{genere}",
            "artista": track['artists'][0]['name'],
            "cancion": track['name'],
            "album": track['album']['name'],
            "year": track['album']['release_date'][:4], 
            "spotify_id": track['id'],
            "popularidad": track['popularity']
        }
        for track in tracks
    ]

# # Función para obtener canciones en múltiples lotes
def busca_pistas(genre, year, limit=50, market="ES"):
    total_pistas = []
    for offset in range(0, 1000, limit):
        results = sp.search(
            q=f"genre:{genre} year:{year}",
            type="track",
            market=market,
            limit=limit,
            offset=offset
        )
        pistas = results['tracks']['items']
        if not pistas:
            break
        total_pistas.extend(get_track_info(pistas, genre))
    return total_pistas


# Obtener canciones llamando a la función
""" pistas_pop_2018 = busca_pistas(genre="pop", year="2018", market="ES")
pistas_pop_2019 = busca_pistas(genre="pop", year="2019", market="ES")
pistas_pop_2020 = busca_pistas(genre="pop", year="2020", market="ES")
pistas_pop_2021 = busca_pistas(genre="pop", year="2021", market="ES")
pistas_pop_2022 = busca_pistas(genre="pop", year="2022", market="ES")
pistas_rock_2018 = busca_pistas(genre="rock", year="2018", market="ES")
pistas_rock_2019 = busca_pistas(genre="rock", year="2019", market="ES")
pistas_rock_2020 = busca_pistas(genre="rock", year="2020", market="ES")
pistas_rock_2021 = busca_pistas(genre="rock", year="2021", market="ES")
pistas_rock_2022 = busca_pistas(genre="rock", year="2022", market="ES")
pistas_electronic_2018 = busca_pistas(genre="electronic", year="2018", market="ES")
pistas_electronic_2019 = busca_pistas(genre="electronic", year="2019", market="ES")
pistas_electronic_2020 = busca_pistas(genre="electronic", year="2020", market="ES")
pistas_electronic_2021 = busca_pistas(genre="electronic", year="2021", market="ES")
pistas_electronic_2022 = busca_pistas(genre="electronic", year="2022", market="ES")
pistas_metal_2018 = busca_pistas(genre="metal", year="2018", market="ES")
pistas_metal_2019 = busca_pistas(genre="metal", year="2019", market="ES")
pistas_metal_2020 = busca_pistas(genre="metal", year="2020", market="ES")
pistas_metal_2021 = busca_pistas(genre="metal", year="2021", market="ES")
pistas_metal_2022 = busca_pistas(genre="metal", year="2022", market="ES") """

# Mostrar resultados
#for pista in pistas_2018:
    #print(f"Canción: {pista['name']}, Artista: {pista['artists'][0]['name']}, Álbum: {pista['album']['name']}")

' pistas_pop_2018 = busca_pistas(genre="pop", year="2018", market="ES")\npistas_pop_2019 = busca_pistas(genre="pop", year="2019", market="ES")\npistas_pop_2020 = busca_pistas(genre="pop", year="2020", market="ES")\npistas_pop_2021 = busca_pistas(genre="pop", year="2021", market="ES")\npistas_pop_2022 = busca_pistas(genre="pop", year="2022", market="ES")\npistas_rock_2018 = busca_pistas(genre="rock", year="2018", market="ES")\npistas_rock_2019 = busca_pistas(genre="rock", year="2019", market="ES")\npistas_rock_2020 = busca_pistas(genre="rock", year="2020", market="ES")\npistas_rock_2021 = busca_pistas(genre="rock", year="2021", market="ES")\npistas_rock_2022 = busca_pistas(genre="rock", year="2022", market="ES")\npistas_electronic_2018 = busca_pistas(genre="electronic", year="2018", market="ES")\npistas_electronic_2019 = busca_pistas(genre="electronic", year="2019", market="ES")\npistas_electronic_2020 = busca_pistas(genre="electronic", year="2020", market="ES")\npistas_electronic_2021 

In [18]:
# Guardamos en un DataFrame
# Definimos una función para poder sacar el Dataframe en todos los géneros y años...

def dataframe(pistas,genre):
    pistas = [
        {
            "artista": pista['artists'][0]['name'],
            "cancion": pista['name'],
            "album": pista['album']['name'],
            "año": pista['album']['release_date'][:4], 
            "genero": f"{genre}",
            "spotify_id": pista['id'],
            "popularidad": pista['popularity']
        }
        for pista in pistas
    ]
    df_genero = pd.DataFrame(pistas)
    df_genero = df_genero.drop_duplicates(subset='spotify_id', keep='first') # Eliminar duplicados
    df_genero.fillna("Sin datos", inplace=True)
    print(df_genero)
    return df_genero


In [48]:
# Llamar a la función y guardar csv con las listas:
lista_generos = ["pop","rock","electronic","metal"]
lista_años = [2018, 2019, 2020, 2021, 2022]

# Crear un diccionario para almacenar los resultados
data = []

for años in lista_años:
    for generos in lista_generos:
        #tracks = busca_pistas(genre={generos}, year={años}, market="ES")
        #pistas_[f"{generos}_{años}"] = busca_pistas(genre=generos, year=años, market="ES")
        data.extend(busca_pistas(generos, años))

#print(json.dumps(data, ensure_ascii=False))
df = pd.DataFrame(data)
df.to_excel(f"./EXCEL/all_tracks.xlsx", index=False)

#df.to_excel(f"./CSV/{generos}/df_{años}.xlsx", index=False)

""" df_pop_2018 = dataframe(pistas_pop_2018,genre="pop")
df_pop_2019 = dataframe(pistas_pop_2019,genre="pop")
df_pop_2020 = dataframe(pistas_pop_2020,genre="pop")
df_pop_2021 = dataframe(pistas_pop_2021,genre="pop")
df_pop_2022 = dataframe(pistas_pop_2022,genre="pop")
df_rock_2018 = dataframe(pistas_rock_2018,genre="rock")
df_rock_2019 = dataframe(pistas_rock_2019,genre="rock")
df_rock_2020 = dataframe(pistas_rock_2020,genre="rock")
df_rock_2021 = dataframe(pistas_rock_2021,genre="rock")
df_rock_2022 = dataframe(pistas_rock_2022,genre="rock")
df_electronic_2018 = dataframe(pistas_electronic_2018,genre="electronic")
df_electronic_2019 = dataframe(pistas_electronic_2019,genre="electronic")
df_electronic_2020 = dataframe(pistas_electronic_2020,genre="electronic")
df_electronic_2021 = dataframe(pistas_electronic_2021,genre="electronic")
df_electronic_2022 = dataframe(pistas_electronic_2022,genre="electronic")
df_metal_2018 = dataframe(pistas_metal_2018,genre="metal")
df_metal_2019 = dataframe(pistas_metal_2019,genre="metal")
df_metal_2020 = dataframe(pistas_metal_2020,genre="metal")
df_metal_2021 = dataframe(pistas_metal_2021,genre="metal")
df_metal_2022 = dataframe(pistas_metal_2022,genre="metal") """

[{"genero": "pop", "artista": "Morat", "cancion": "Cuando Nadie Ve", "album": "Balas Perdidas", "year": "2018", "spotify_id": "71iAechwVKGu26pahzFL0k", "popularidad": 76}, {"genero": "pop", "artista": "Sia", "cancion": "Snowman", "album": "Everyday Is Christmas (Deluxe Edition)", "year": "2018", "spotify_id": "7uoFMmxln0GPXQ0AcCBXRq", "popularidad": 91}, {"genero": "pop", "artista": "Morat", "cancion": "Besos En Guerra", "album": "Balas Perdidas", "year": "2018", "spotify_id": "1mlGScrDQqHqmhdIqE8MmA", "popularidad": 75}, {"genero": "pop", "artista": "Morat", "cancion": "No Se Va", "album": "Balas Perdidas", "year": "2018", "spotify_id": "4khWEpnaijN0G1x019Uzdr", "popularidad": 77}, {"genero": "pop", "artista": "Manuel Carrasco", "cancion": "Qué Bonito Es Querer", "album": "La Cruz Del Mapa", "year": "2018", "spotify_id": "6uzGmmQ4CuG9HvZktEy0LF", "popularidad": 61}, {"genero": "pop", "artista": "Melendi", "cancion": "Destino o casualidad", "album": "Destino o casualidad", "year": "201

' df_pop_2018 = dataframe(pistas_pop_2018,genre="pop")\ndf_pop_2019 = dataframe(pistas_pop_2019,genre="pop")\ndf_pop_2020 = dataframe(pistas_pop_2020,genre="pop")\ndf_pop_2021 = dataframe(pistas_pop_2021,genre="pop")\ndf_pop_2022 = dataframe(pistas_pop_2022,genre="pop")\ndf_rock_2018 = dataframe(pistas_rock_2018,genre="rock")\ndf_rock_2019 = dataframe(pistas_rock_2019,genre="rock")\ndf_rock_2020 = dataframe(pistas_rock_2020,genre="rock")\ndf_rock_2021 = dataframe(pistas_rock_2021,genre="rock")\ndf_rock_2022 = dataframe(pistas_rock_2022,genre="rock")\ndf_electronic_2018 = dataframe(pistas_electronic_2018,genre="electronic")\ndf_electronic_2019 = dataframe(pistas_electronic_2019,genre="electronic")\ndf_electronic_2020 = dataframe(pistas_electronic_2020,genre="electronic")\ndf_electronic_2021 = dataframe(pistas_electronic_2021,genre="electronic")\ndf_electronic_2022 = dataframe(pistas_electronic_2022,genre="electronic")\ndf_metal_2018 = dataframe(pistas_metal_2018,genre="metal")\ndf_metal

In [29]:
#CREAMOS FUNCION PARA NO REPETIR ARTISTA
def lista_artistas(pistas, genre):

    lista_artistas = []

    for pista in pistas:
        lista_artistas.append(pista['artists'][0]['name'])

    df_lista_artistas = pd.DataFrame(lista_artistas)
    df_lista_artistas = df_lista_artistas.drop_duplicates(keep='first') # Eliminar duplicados
    df_lista_artistas['Genero'] = f"{genre}"
    print(df_lista_artistas)
    return df_lista_artistas

In [ ]:
#LLAMAR
lista_artistas_pop_2018 = lista_artistas(pistas_pop_2018,genre="Pop")
lista_artistas_pop_2019 = lista_artistas(pistas_pop_2019,genre="Pop")
lista_artistas_pop_2020 = lista_artistas(pistas_pop_2020,genre="Pop")
lista_artistas_pop_2021 = lista_artistas(pistas_pop_2021,genre="Pop")
lista_artistas_pop_2022 = lista_artistas(pistas_pop_2022,genre="Pop")
lista_artistas_rock_2018 = lista_artistas(pistas_rock_2018,genre="Rock")
lista_artistas_rock_2019 = lista_artistas(pistas_rock_2019,genre="Rock")
lista_artistas_rock_2020 = lista_artistas(pistas_rock_2020,genre="Rock")
lista_artistas_rock_2021 = lista_artistas(pistas_rock_2021,genre="Rock")
lista_artistas_rock_2022 = lista_artistas(pistas_rock_2022,genre="Rock")
lista_artistas_electronic_2018 = lista_artistas(pistas_electronic_2018,genre="Electronic")
lista_artistas_electronic_2019 = lista_artistas(pistas_electronic_2019,genre="Electronic")
lista_artistas_electronic_2020 = lista_artistas(pistas_electronic_2020,genre="Electronic")
lista_artistas_electronic_2021 = lista_artistas(pistas_electronic_2021,genre="Electronic")
lista_artistas_electronic_2022 = lista_artistas(pistas_electronic_2022,genre="Electronic")
lista_artistas_metal_2018 = lista_artistas(pistas_metal_2018,genre="Metal")
lista_artistas_metal_2019 = lista_artistas(pistas_metal_2019,genre="Metal")
lista_artistas_metal_2020 = lista_artistas(pistas_metal_2020,genre="Metal")
lista_artistas_metal_2021 = lista_artistas(pistas_metal_2021,genre="Metal")
lista_artistas_metal_2022 = lista_artistas(pistas_metal_2022,genre="Metal")

                   0 Genero
0              Morat    Pop
1                Sia    Pop
4    Manuel Carrasco    Pop
5            Melendi    Pop
6          Lady Gaga    Pop
..               ...    ...
990      Kaan Boşnak    Pop
993          DZIDZIO    Pop
995   Hiphop Tamizha    Pop
997    Yasmin Santos    Pop
998          Nielson    Pop

[580 rows x 2 columns]
                  0 Genero
0    Dani Fernández    Pop
1     Lewis Capaldi    Pop
2             Leiva    Pop
3       Danny Ocean    Pop
4      Taylor Swift    Pop
..              ...    ...
991             Jão    Pop
993     Tony Kakkar    Pop
994      Okean Elzy    Pop
996       Harmonize    Pop
999  Diljit Dosanjh    Pop

[547 rows x 2 columns]
                  0 Genero
0    La La Love You    Pop
1    Rauw Alejandro    Pop
2       Arde Bogotá    Pop
3        The Weeknd    Pop
4            Maluma    Pop
..              ...    ...
994   Emma Heesters    Pop
995           Einár    Pop
996        Bahh Tee    Pop
998          Hasibe   

In [33]:
#CREAMOS FUNCION PARA NO REPETIR ALBUMES
def lista_albumes(pistas,genre):

    lista_albumes = []

    for pista in pistas:
        lista_albumes.append(pista['album']['name'])

    df_lista_albumes = pd.DataFrame(lista_albumes)
    df_lista_albumes = df_lista_albumes.drop_duplicates(keep='first') # Eliminar duplicados
    df_lista_albumes['Genero'] = f"{genre}"
    
    print(df_lista_albumes)
    return df_lista_albumes

In [34]:
df_lista_albumes_pop_2018 = lista_albumes(pistas_pop_2018,genre="Pop")
df_lista_albumes_pop_2019 = lista_albumes(pistas_pop_2019,genre="Pop")
df_lista_albumes_pop_2020 = lista_albumes(pistas_pop_2020,genre="Pop")
df_lista_albumes_pop_2021 = lista_albumes(pistas_pop_2021,genre="Pop")
df_lista_albumes_pop_2022 = lista_albumes(pistas_pop_2022,genre="Pop")
df_lista_albumes_rock_2018 = lista_albumes(pistas_rock_2018,genre="Rock")
df_lista_albumes_rock_2019 = lista_albumes(pistas_rock_2019,genre="Rock")
df_lista_albumes_rock_2020 = lista_albumes(pistas_rock_2020,genre="Rock")
df_lista_albumes_rock_2021 = lista_albumes(pistas_rock_2021,genre="Rock")
df_lista_albumes_rock_2022 = lista_albumes(pistas_rock_2022,genre="Rock")
df_lista_albumes_electronic_2018 = lista_albumes(pistas_electronic_2018,genre="Electronic")
df_lista_albumes_electronic_2019 = lista_albumes(pistas_electronic_2019,genre="Electronic")
df_lista_albumes_electronic_2020 = lista_albumes(pistas_electronic_2020,genre="Electronic")
df_lista_albumes_electronic_2021 = lista_albumes(pistas_electronic_2021,genre="Electronic")
df_lista_albumes_electronic_2022 = lista_albumes(pistas_electronic_2022,genre="Electronic")
df_lista_albumes_metal_2018 = lista_albumes(pistas_metal_2018,genre="Metal")
df_lista_albumes_metal_2019 = lista_albumes(pistas_metal_2019,genre="Metal")
df_lista_albumes_metal_2020 = lista_albumes(pistas_metal_2020,genre="Metal")
df_lista_albumes_metal_2021 = lista_albumes(pistas_metal_2021,genre="Metal")
df_lista_albumes_metal_2022 = lista_albumes(pistas_metal_2022,genre="Metal")


                                                     0 Genero
0                                       Balas Perdidas    Pop
1               Everyday Is Christmas (Deluxe Edition)    Pop
4                                     La Cruz Del Mapa    Pop
5                                 Destino o casualidad    Pop
6                            A Star Is Born Soundtrack    Pop
..                                                 ...    ...
994                                       Última Noite    Pop
995  Imaikkaa Nodigal (Original Motion Picture Soun...    Pop
996                                               Culo    Pop
997                                 Saudade Nível Hard    Pop
998                                            Diamant    Pop

[681 rows x 2 columns]
                                           0 Genero
0                                  Incendios    Pop
1    Divinely Uninspired To A Hellish Extent    Pop
2                                    Nuclear    Pop
3                       

In [35]:
total_pistas = pd.concat([df_electronic_2018, df_pop_2018, df_rock_2018, df_metal_2018, df_electronic_2019, df_pop_2019, df_rock_2019, df_metal_2019, df_electronic_2020, df_pop_2020, df_rock_2020, df_metal_2020, df_electronic_2021, df_pop_2021, df_rock_2021, df_metal_2021, df_electronic_2022, df_pop_2022, df_rock_2022, df_metal_2022])
print(total_pistas)
total_pistas.to_csv("./CSV/20000_pistas.csv", index=False)
total_pistas.to_excel("./EXCEL/20000_pistas.xlsx", index=False)

total_artistas = pd.concat([lista_artistas_electronic_2018, lista_artistas_pop_2018, lista_artistas_rock_2018, lista_artistas_metal_2018, lista_artistas_electronic_2019, lista_artistas_pop_2019, lista_artistas_rock_2019, lista_artistas_metal_2019, lista_artistas_electronic_2020, lista_artistas_pop_2020, lista_artistas_rock_2020, lista_artistas_metal_2020, lista_artistas_electronic_2021, lista_artistas_pop_2021, lista_artistas_rock_2021, lista_artistas_metal_2021, lista_artistas_electronic_2022, lista_artistas_pop_2022, lista_artistas_rock_2022, lista_artistas_metal_2022])
print(total_artistas)
total_artistas.to_csv("./CSV/total_artistas.csv", index=False)
total_artistas.to_excel("./EXCEL/total_artistas.xlsx", index=False)

total_albumes = pd.concat([df_lista_albumes_electronic_2018, df_lista_albumes_pop_2018, df_lista_albumes_rock_2018, df_lista_albumes_metal_2018, df_lista_albumes_electronic_2019, df_lista_albumes_pop_2019, df_lista_albumes_rock_2019, df_lista_albumes_metal_2019, df_lista_albumes_electronic_2020, df_lista_albumes_pop_2020, df_lista_albumes_rock_2020, df_lista_albumes_metal_2020, df_lista_albumes_electronic_2021, df_lista_albumes_pop_2021, df_lista_albumes_rock_2021, df_lista_albumes_metal_2021, df_lista_albumes_electronic_2022, df_lista_albumes_pop_2022, df_lista_albumes_rock_2022, df_lista_albumes_metal_2022])
print(total_albumes)
total_albumes.to_csv("./CSV/total_albumes.csv", index=False)
total_albumes.to_excel("./EXCEL/total_albumes.xlsx", index=False)

                  artista                                         cancion  \
0                DJ Snake  Taki Taki (with Selena Gomez, Ozuna & Cardi B)   
1           Maribou State                                            Vale   
2                  Xinobi                    Far Away Place - Rampa Remix   
3                    Rhye                                    Song For You   
4                    Rhye               Feel Your Weight - Poolside Remix   
..                    ...                                             ...   
995          Foo Fighters                                        Everlong   
996  Harakiri for the Sky                                       Mad World   
997         Dropout Kings                              GlitchGang (Remix)   
998            Papa Roach                                Always Wandering   
999            Papa Roach                                       Bloodline   

                                              album   año      genero  \
0 